# EIS Fire IMERG FWI Notebook 1.1.0
### Version: 05.06.21
EIS – Fire: IMERG/GOES Notebooks aims to create interactive visualizations of IMERG and other raster data. These are interactive visualizations of raster data in conjunction with vector layers with added functionality including (but not limited to) time-series averages, animations.

For customization of color maps for visuals, see the following link for options: https://matplotlib.org/stable/tutorials/colors/colormaps.html

In [1]:
from datetime import datetime
import io
import numpy as np
import pandas
import requests
import s3fs
import warnings
import xarray as xr
import zipfile

import cartopy.crs as ccrs
import colorcet as cc
import geopandas as gpd
import holoviews as hv
import hvplot.pandas
import hvplot.xarray
import panel as pn
import rioxarray as rxr
from shapely.geometry import mapping

from sqlalchemy.ext.automap import automap_base
from sqlalchemy.orm import Session, sessionmaker, declarative_base
from sqlalchemy import create_engine, MetaData, Table, inspect
from sqlalchemy import select, func

xr.set_options(display_style="html")
warnings.filterwarnings('ignore')
pn.extension()

### postgresql login credentials

In [2]:
username = 'guest'
password = 'fires'
host = 'eis-fire-db.ccgflq7ivofg.us-east-1.rds.amazonaws.com'
database = 'eisfire'
engine = 'postgresql://{}:{}@{}/{}'.format(username, password, host, database)

### Datasets

Add, modify or remove the desired Zarr dataset file. Following the convention:
`"DATASET" : "path/to/zarr/file.zarr"`

In [3]:
raster_filepath = {
    'IMERG': "eis-dh-fire/imerg-fwi.zarr",
    'GOES FP': "eis-dh-fire/geos-fp-zarr/conus.zarr"
}

## User-defined variables

Add, modify, or remove variables below. Please follow conventions outlined in comments.

In [4]:
# IGNORE THIS
engine = create_engine(engine)
Base = automap_base()
Base.prepare(engine, reflect=True)
Fires = Base.classes.fires
States = Base.classes.tl_2020_us_state
Countries = Base.classes.tl_2020_us_county
# END IGNORE THIS

# ---
# Variables from raster datasets to use.
# Follow {'DATASET': ['var1', 'var2'],
#         'DATASET': ['var1', 'var2']
# ---
raster_variables = {
    'IMERG': ['IMERG.FINAL.v6_FWI'],
    'GOES FP': ['T2M']
}

raster_variable_to_show = 'IMERG.FINAL.v6_FWI' # 'T2M'

# If desired, slice time to date_start and date_end.
date_start = '2020-06-06'
date_end = '2020-09-01'

# Date to use with below query
date = '2020-07-11'

# State abreviation to use with below query
place = 'CA'

# Post-gres query to be used to retrieve shape data points (active fires for example).
marker_query = (select(Fires).
                join(States, func.ST_CONTAINS(
                    States.geom, 
                    func.ST_TRANSFORM(Fires.geom, func.ST_SRID(States.geom)))).
               where(func.date_trunc('day', Fires.image_datetime) == date,
                    States.stusps == place)
               )

# Post-gres query to be used to retrieve a polygon shape layer.
layer_query = select(States).filter_by(stusps = place)

# See ____ for more projection options.
projection = ccrs.PlateCarree()

# Set to True if user would like to clip raster to land only.
clip_to_land = True

# If time_average is true, which time step to average.
# Month = 'time.month'
# Day = 'time.dayofyear'
time_step = 'time.month'

# If animated is true, which time step to use.
# Month = 'M'
# Day = 'D'
# 6 hr = '6H'
animated_time_step = 'D'

# If anomaly_map is True, which time step to base map off of.
# Month = 'time.month'
# Day = 'time.dayofyear'
anomaly_time_step = 'time.month'

In [5]:
tbounds = slice(date_start, date_end)
states = ["AL", "AK", "AZ", "AR", "CA", "CO", "CT", "DC", "DE", "FL", "GA", 
          "HI", "ID", "IL", "IN", "IA", "KS", "KY", "LA", "ME", "MD", 
          "MA", "MI", "MN", "MS", "MO", "MT", "NE", "NV", "NH", "NJ", 
          "NM", "NY", "NC", "ND", "OH", "OK", "OR", "PA", "RI", "SC", 
          "SD", "TN", "TX", "UT", "VT", "VA", "WA", "WV", "WI", "WY"]
markercolor_iter = ['r', 'b', 'g', 'k', 'z']
daterange_iter = list(pandas.date_range(tbounds.start, tbounds.stop))
update_iter = [False, True]
cmaps  = {n: cc.palette[n] for n in ['kbc', 'fire', 'bgy', 'bgyw', 'bmy', 'gray', 'kbc']}

# Reads in a land mask to clip user-defined rasters to.
land_shp = None
if clip_to_land:
    land_shp = gpd.read_file('./shape_files/LandMask/ne_110m_land.shp')

s3 = s3fs.S3FileSystem(anon=False)
dataset_path = {}
for dataset, path in raster_filepath.items():
    print(dataset, path)
    dataset_path[dataset] = s3.get_mapper(path)

zarrDict = {}
for mission, s3_file in dataset_path.items():
    print(mission, s3_file)
    zarrDict[mission] = xr.open_zarr(s3_file, consolidated=True)

datasetSubs = {}
for mission, dataset in raster_variables.items():
    for subdataset in dataset:
        if mission not in datasetSubs.keys():
            datasetSubs[mission] = {}
        datasetSubs[mission] = { subdataset : zarrDict[mission][subdataset]}

IMERG eis-dh-fire/imerg-fwi.zarr
GOES FP eis-dh-fire/geos-fp-zarr/conus.zarr
IMERG <fsspec.mapping.FSMap object at 0x7fbf520a43a0>
GOES FP <fsspec.mapping.FSMap object at 0x7fbf5208d3d0>


## Dataset-specific modifications

In [6]:
datasetSubs['GOES FP']['T2M'] = datasetSubs['GOES FP']['T2M'].resample(time='1D').mean("time").sel(time=tbounds)
datasetSubs['IMERG']['IMERG.FINAL.v6_FWI'] = datasetSubs['IMERG']['IMERG.FINAL.v6_FWI'].sel(time=tbounds).interp_like(datasetSubs['GOES FP']['T2M'])

In [7]:
mergedDataset = None
for mission, dataDict in datasetSubs.items():
    for subd, array in dataDict.items():
        if mergedDataset is None:
            mergedDataset = array
        mergedDataset = xr.merge([mergedDataset, array])

### Functions to query and read shape layers and data

In [8]:
def get_shp_layer(engine, place):
    # INSERT CUSTOM LAYER QUERY HERE
    state_query = select(States).filter_by(stusps = place)
    # ENG INSERT CUSTOM QUERY HERE
    shpLayer = gpd.read_postgis(state_query, engine)
    shpLayer = shpLayer.rename_geometry('geometry', inplace=False)
    return shpLayer

def get_shp_data(date, engine, place='CA'):
    date = pandas.to_datetime(str(date))
    date = date.strftime('%Y-%m-%d')
    ### INSERT CUSTOM MARKER QUERY HERE
    fire_query = (select(Fires).
                join(States, func.ST_CONTAINS(
                    States.geom, 
                    func.ST_TRANSFORM(Fires.geom, func.ST_SRID(States.geom)))).
               where(func.date_trunc('day', Fires.image_datetime) == date,
                    States.stusps == place)
               )
    # END INSERT CUSTOM QUERY HERE
    shpData = gpd.read_postgis(fire_query, engine)
    shpData = shpData.rename_geometry('geometry', inplace=False)
    return shpData

### Clip raster to land mask

In [9]:
def clip_to_shape(raster, shape_file):
    raster.rio.set_spatial_dims(x_dim="lon", y_dim="lat", inplace=True)
    raster.rio.write_crs("epsg:4326", inplace=True)
    raster_clipped = raster.rio.clip(shape_file.geometry.apply(mapping), shape_file.crs, drop=False)
    return raster_clipped

In [10]:
main_raster = clip_to_shape(mergedDataset[raster_variable_to_show], land_shp)
main_raster_list = [main_raster]

In [11]:
def get_clim(data_array):
    da_min = data_array.min(dim=['lat', 'lon', 'time']).load()
    da_max = data_array.max(dim=['lat', 'lon', 'time']).load()
    return (da_min, da_max)

def get_clim_time_averaged(data_array):
    da_min = data_array.min(dim=['lat', 'lon', 'month']).load()
    da_max = data_array.max(dim=['lat', 'lon', 'month']).load()
    return (da_min, da_max)

In [12]:
main_raster_clim = get_clim(main_raster)

In [13]:
shp_data = gpd.read_postgis(marker_query, engine)
shp_data_one = shp_data.rename_geometry('geometry', inplace=False)

shp_layer = gpd.read_postgis(layer_query, engine)
shp_layer_one = shp_layer.rename_geometry('geometry', inplace=False)

# Visualization 1 - Interactive plot with coastline overlay

This is a basic interactive plot. The widget at the bottom of the plot allows you to scroll through individual days.

The controls on the right allow you to zoom, move around, and save the visual. Hover over the visual to see variables.

In [17]:
# If custom colorbar range desired, then set the following variables.

# True or False
custom_range_bool_v1 = True

# (lower_bound, upper_bound)
custom_range_v1 = (0, 60)

In [18]:
def visual_one(cmap, dt):
    raster_to_use = main_raster
    raster_clim = custom_range_v1 if custom_range_bool_v1 else main_raster_clim
    raster = raster_to_use.sel(time=dt).hvplot(
        cmap=cmap,
        coastline=True,
        frame_width=600,
        clim=raster_clim,
        projection=projection,
    )
    date_to_show = pandas.to_datetime(str(dt))
    dt_str = date_to_show.strftime('%m-%d-%Y')
    plot = (raster).opts(title='{} Date: {}'.format(raster_variable_to_show, dt_str))
    return plot    

In [19]:
kdims_list = ['cmap', 'dt']
dynamic_viz_1 = hv.DynamicMap(visual_one, kdims=kdims_list)
dynamic_viz_1.redim.values(cmap=cmaps, dt=daterange_iter)

:DynamicMap   [cmap,dt]
   :Overlay
      .Image.I     :Image   [lon,lat]   (IMERG.FINAL.v6_FWI)
      .Coastline.I :Feature   [Longitude,Latitude]

## Visualization 2 - Raster with shape layer

Raster layer with user-defined vector/shape layer. Users may define their own vector/shape layer as long as it is GeoPandas readable. 

The controls on the right allow you to zoom, move around, and save the visual. Hover over the visual to see variables.

In [23]:
# If custom colorbar range desired, then set the following variables.

# True or False
custom_range_bool_v2 = False

# (lower_bound, upper_bound)
custom_range_v2 = (250, 300)

In [24]:
def visual_two(cmap, dt, marker_color, state, update_location):
    
    date_to_show = pandas.to_datetime(str(dt))
    dt_str = date_to_show.strftime('%d-%m-%Y')
    raster_clim = custom_range_v2 if custom_range_bool_v2 else main_raster_clim
    if not update_location:
        raster_to_use = main_raster
        shp_layer = shp_layer_one
        shp_data = shp_data_one
    
        raster = raster_to_use.sel(time=dt).hvplot(
            cmap=cmap,
            coastline=False,
            frame_width=800,
            clim=raster_clim,
            projection=projection)
    
    if update_location:
        shp_layer = get_shp_layer(engine, state)
        raster_clipped = clip_to_shape(main_raster, shp_layer)
        raster_clim_clipped = get_clim(raster_clipped)
        raster_clim = custom_range_v2 if custom_range_bool_v2 else raster_clim_clipped
        raster = raster_clipped.sel(time=dt).hvplot(
            cmap=cmap,
            coastline=False,
            frame_width=800,
            clim=raster_clim,
            projection=projection)
        
        shp_data = get_shp_data(dt, engine, place=state)
    
    points = shp_data.hvplot.points(
        frame_width=800,
        projection=projection,
        marker='+',
        color=marker_color)
    
    layer = shp_layer.hvplot(
        frame_width=800,
        #projection=projection,
        color='None')
    
    plot = (raster * points * layer).opts(title='{} Date: {}'.format(raster_variable_to_show, dt_str))
    
    return plot

In [25]:
kdims_list = ['cmap', 'dt', 'marker_color', 'state', 'update_location']
dynamic_viz_2 = hv.DynamicMap(visual_two, kdims=kdims_list)
dynamic_viz_2.redim.values(cmap=cmaps, dt=daterange_iter, marker_color=markercolor_iter,
                          state=states, update_location=update_iter)

:DynamicMap   [cmap,dt,marker_color,state,update_location]
   :Overlay
      .Image.I    :Image   [lon,lat]   (IMERG.FINAL.v6_FWI)
      .Points.I   :Points   [Longitude,Latitude]
      .Polygons.I :Polygons   [x,y]

## Visualization 3 - Time-averaged plot

Averaged by time-step defined in code cell five. Use the scroll bar at the bottom to scrub through time.

The controls on the right allow you to zoom, move around, and save the visual. Hover over the visual to see variables.

In [30]:
# If custom colorbar range desired, then set the following variables.

# True or False
custom_range_bool_v3 = True

# (lower_bound, upper_bound)
custom_range_v3 = (0, 60)

In [31]:
time_averaged = main_raster.groupby(time_step).mean('time')
ta_list = np.asarray(time_averaged.month)

In [54]:
def visual_three(cmap, month):
    raster_to_use = time_averaged.sel(month=month)
    raster_clim = custom_range_v3 if custom_range_bool_v3 else main_raster_clim
    raster = raster_to_use.hvplot(
        coastline=True,
        clim=raster_clim,
        cmap=cmap,
        frame_width=800)
    plot = raster
    plot.opts(title='{} Time-Averaged, Month: {}'.format(raster_variable_to_show, month))
    return plot

In [55]:
kdims_list_3 = ['cmap', 'month']
dynamic_viz_3 = hv.DynamicMap(visual_three, kdims=kdims_list_3)
dynamic_viz_3.redim.values(cmap=cmaps, month=ta_list)

:DynamicMap   [cmap,month]
   :Overlay
      .Image.I     :Image   [lon,lat]   (IMERG.FINAL.v6_FWI)
      .Coastline.I :Feature   [Longitude,Latitude]

## Visualization 4 - Dynamic time-averaged plot with shape file overlay

Use the controls to the right of the visual to zoom, move around, and save the visual.

In [36]:
# If custom colorbar range desired, then set the following variables.

# True or False
custom_range_bool_v4 = False

# (lower_bound, upper_bound)
custom_range_v4 = (250, 300)

In [37]:
def visual_four(cmap, month, state, update_location):
    
    if not update_location:
        raster_to_use = time_averaged
        shp_layer = shp_layer_one
        raster_clim = custom_range_v4 if custom_range_bool_v4 else main_raster_clim
    
        raster = raster_to_use.sel(month=month).hvplot(
            cmap=cmap,
            coastline=True,
            frame_width=800,
            clim=raster_clim,
            projection=projection)
    
    if update_location:
        shp_layer = get_shp_layer(engine, state)
        raster_clipped = clip_to_shape(time_averaged, shp_layer)
        raster_clim = get_clim_time_averaged(raster_clipped) if not custom_range_bool_v4 else custom_range_v4
        raster = raster_clipped.sel(month=month).hvplot(
            cmap=cmap,
            coastline=True,
            frame_width=800,
            clim=raster_clim,
            projection=projection)
    
    layer = shp_layer.hvplot(
        frame_width=800,
        color='None')
    
    plot = (raster * layer).opts(title='{} Time-Averaged, Month: {}'.format(raster_variable_to_show, month))
    
    return plot

In [38]:
kdims_list_four = ['cmap', 'month', 'state', 'update_location']
dynamic_viz_4 = hv.DynamicMap(visual_four, kdims=kdims_list_four)
dynamic_viz_4.redim.values(cmap=cmaps, month=ta_list, state=states, update_location=update_iter)

:DynamicMap   [cmap,month,state,update_location]
   :Overlay
      .Image.I     :Image   [lon,lat]   (IMERG.FINAL.v6_FWI)
      .Coastline.I :Feature   [Longitude,Latitude]
      .Polygons.I  :Polygons   [x,y]

## Visualization 5 - Animation by time step

Time series animation. It should be noted that if rasters are particularly large, then the animation will run slow and may skip time steps.

Use the play/pause widget to play through the animation. Be aware that calculations can make the animation lag at times.

In [40]:
# If custom colorbar range desired, then set the following variables.

# True or False
custom_range_bool_v5 = True

# (lower_bound, upper_bound)
custom_range_v5 = (0, 60)

In [41]:
color_map='cool'

In [42]:
animationDataset = main_raster.resample(time=animated_time_step).mean('time')
raster_clim = custom_range_v5 if custom_range_bool_v5 else main_raster_clim

In [43]:
plot_5 = animationDataset.hvplot(
    groupby='time',
    cmap=color_map,
    coastline=True,
    frame_width=800,
    clim=raster_clim,
    projection=projection,
    widget_type='scrubber',
    widget_location='bottom')
plot_5

Column
    [0] HoloViews(DynamicMap, widget_location='bottom', widget_type='scrubber')
    [1] Row
        [0] HSpacer()
        [1] WidgetBox
            [0] Player(end=87, width=550)
        [2] HSpacer()

## Visualization 6 - Anomaly Maps

Use the scrubber widget at the bottom to move through time by anomaly time-step defined in code cell five.

Controls to the right of the visual allow you to zoom, move, and save. Hover over the visual to see the variable on-hover.

In [44]:
# If custom colorbar range desired, then set the following variables.

# True or False
custom_range_bool_v6 = False

# (lower_bound, upper_bound)
custom_range_v6 = (0, 5)

In [45]:
anomaly = main_raster.groupby(anomaly_time_step) - \
    main_raster.groupby(anomaly_time_step).mean('time')

In [46]:
def visual_six(cmap, dt, state, update_location):
    raster_clim = get_clim(anomaly) if not custom_range_bool_v6 else custom_range_v6
    if not update_location:
        raster_to_use = anomaly
        shp_layer = shp_layer_one
    
        raster = raster_to_use.sel(time=dt).hvplot(
            cmap=cmap,
            coastline=True,
            frame_width=800,
            clim=raster_clim,
            projection=projection)
    
    if update_location:
        shp_layer = get_shp_layer(engine, state)
        raster_clipped = clip_to_shape(anomaly, shp_layer)
        anomaly_clim = custom_range_v6 if custom_range_bool_v6 else get_clim(raster_clipped)
        raster = raster_clipped.sel(time=dt).hvplot(
            cmap=cmap,
            coastline=True,
            frame_width=800,
            clim=anomaly_clim,
            projection=projection)
    
    layer = shp_layer.hvplot(
        frame_width=800,
        color='None')
    
    plot = (raster * layer).opts(title='{} Anomaly, Dt: {}'.format(raster_variable_to_show, dt))
    
    return plot

In [47]:
kdims_list_six = ['cmap', 'dt', 'state', 'update_location']
dynamic_viz_six = hv.DynamicMap(visual_six, kdims=kdims_list_six)
dynamic_viz_six.redim.values(cmap=cmaps, dt=daterange_iter, state=states, update_location=update_iter)

:DynamicMap   [cmap,dt,state,update_location]
   :Overlay
      .Image.I     :Image   [lon,lat]   (IMERG.FINAL.v6_FWI)
      .Coastline.I :Feature   [Longitude,Latitude]
      .Polygons.I  :Polygons   [x,y]

## Visualization 7 - Lat/Lon averaged per day.

Use the controls to the right of the visual to zoom, move around, and save.

In [48]:
main_raster.hvplot.scatter('time', groupby=[], datashade=True) *\
main_raster.mean(['lat', 'lon']).hvplot.line('time', color='indianred')

:DynamicMap   []
   :Overlay
      .RGB.I   :RGB   [time,IMERG.FINAL.v6_FWI]   (R,G,B,A)
      .Curve.I :Curve   [time]   (IMERG.FINAL.v6_FWI)

## Visualization 8 - User-defined polygon

In [49]:
# If custom colorbar range desired, set the following variables.

# True or False
custom_range_bool_v8 = False

# (lower_bound, upper_bound)
custom_range_v8 = (250, 290)

In [50]:
from ipyleaflet import Map, basemaps, basemap_to_tiles, DrawControl

visual_iter = ['Raster Variable', 'Time-Averaged (month)', 'Anomaly']
watercolor = basemap_to_tiles(basemaps.CartoDB.DarkMatter)

m = Map(layers=(watercolor, ), center=(39.59, -98.26), zoom=4)

draw_control = DrawControl()

draw_control.polygon = {
    "shapeOptions": {
        "fillColor": "#6be5c3",
        "color": "#6be5c3",
        "fillOpacity": 0.2
    },
    "drawError": {
        "color": "#dd253b",
        "message": "Oups!"
    },
    "allowIntersection": False
}

draw_control.rectangle = {
    "shapeOptions": {
        "fillColor": "#fca45d",
        "color": "#fca45d",
        "fillOpacity": 0.2
    }
}

feature_collection = {
    'type': 'FeatureCollection',
    'features': []
}

def handle_draw(self, action, geo_json):
    """Do something with the GeoJSON when it's drawn on the map"""
    feature_collection['features'].append(geo_json)

draw_control.on_draw(handle_draw)
m.add_control(draw_control)

m


Map(center=[39.59, -98.26], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_…

In [51]:
df = gpd.GeoDataFrame.from_features(feature_collection)

In [52]:
def visual_eight(Color_Map, Date_Time):
    
    date_to_show = pandas.to_datetime(str(Date_Time))
    dt_str = date_to_show.strftime('%m-%d-%Y')
    raster_clim = custom_range_v8 if custom_range_bool_v8 else main_raster_clim
    
    shp_layer = df
    raster_clipped = clip_to_shape(main_raster, shp_layer)
        
    raster = raster_clipped.sel(time=Date_Time).hvplot(
        cmap=Color_Map,
        coastline=True,
        frame_width=800,
        clim=raster_clim,
        projection=projection)
    
    layer = shp_layer.hvplot(
        frame_width=800,
        color='None')
    
    plot = (raster * layer).opts(title='{} Date: {}'.format(raster_variable_to_show, dt_str))
    
    return plot

In [53]:
kdims_list_eight = ['Color_Map', 'Date_Time']
dynamic_viz_8 = hv.DynamicMap(visual_eight, kdims=kdims_list_eight)
dynamic_viz_8.redim.values(Color_Map=cmaps, Date_Time=daterange_iter)

:DynamicMap   [Color_Map,Date_Time]
   :Overlay
      .Image.I     :Image   [lon,lat]   (IMERG.FINAL.v6_FWI)
      .Coastline.I :Feature   [Longitude,Latitude]
      .Polygons.I  :Polygons   [x,y]